# Batch process Equivalent Widths with MCMC

The goal of this notebook is to distill our analysis into a programmatic loop over many spectra and save the Equivalent Width (EW) and its uncertainty to a results table.  The table will be in the form of a pandas dataframe, which we'll then save as a csv file.

In [33]:
import os

import numpy as np
import pandas as pd
import os
import glob
from astropy.io import fits
import emcee
from astropy.time import Time
from tqdm.auto import tqdm

import warnings

import pandas as pd
from pandas.core.common import SettingWithCopyWarning

warnings.simplefilter(action="ignore", category=SettingWithCopyWarning)

In [34]:
import warnings

import pandas as pd
from pandas.core.common import SettingWithCopyWarning

warnings.simplefilter(action="ignore", category=SettingWithCopyWarning)

In [35]:
goldilocks_files = glob.glob('C:/Users/jojoa/GitHub/disperse/data/HPF/Helium-transit-data/**/Goldilocks*.fits', recursive=True)

In [36]:
target_name = 'HAT-P-67b'
matchers = [target_name]
matching = [s for s in goldilocks_files if any(xs in s for xs in matchers)]
goldilocks_files = matching

In [37]:
filename_zero = goldilocks_files[0]
hdus = fits.open(filename_zero)

In [38]:
def get_goldilocks_dataframe(fn):
    """Return a pandas Dataframe given a Goldilocks FITS file name"""
    hdus = fits.open(fn)
    df_original = pd.DataFrame()
    header = hdus[0].header
    for j in range(28):
        df = pd.DataFrame()
        for i in range(1, 10):
            name = hdus[i].name
            df[name] = hdus[i].data[j, :]
        df['order'] = j
        df_original = df_original.append(df, ignore_index=True)
    keep_mask = df_original[df_original.columns[0:6]] != 0.0
    df_original = df_original[keep_mask.all(axis=1)].reset_index(drop=True)
    
    return df_original, header

In [39]:
def normalize_spectrum(df):
    """Normalizes spectrum to set to one"""
    for order in df.order.unique():
        mask = df.order == order
        norm_constant = df['Sci Flux'][mask].median() #mean takes outliers into account
        df['Sci Flux'][mask] = df['Sci Flux'][mask]/norm_constant
        df['Sci Error'][mask] = df['Sci Error'][mask]/norm_constant
        
    return df

Eventually we will loop over index.

In [40]:
order = 4
n_walkers = 32
n_params = 5
n_steps = 5000
labels = ["m", "b", "A", "mu", "w"]

In [41]:
df_results = pd.DataFrame()

In [42]:
for index in tqdm(range(0, len(goldilocks_files)),position=0, leave=True):
#for index in tqdm(range(0, 5)):
    
    fn = goldilocks_files[index]
    print(index, fn[-49:])
    df_orig, header = get_goldilocks_dataframe(fn)
    date_raw = header['DATE-OBS']
    date = date_raw[0:10]
    time = date_raw[11:19]
    obj = header['OBJECT']
    df = normalize_spectrum(df_orig)
    qidx = header['QIDX']
    j_date = date_raw
    t = Time(j_date, format='isot', scale='utc')
    jd = t.jd
    
    calcium_line = 8542 #8961 is Fe I
    wavelength1 = calcium_line*0.999
    wavelength2 = calcium_line*1.001
    
    sub_region = (df.order == order) & (df['Sci Wavl'] > wavelength1) & (df['Sci Wavl'] < wavelength2)
    wl = df['Sci Wavl'][sub_region].values
    flux = df['Sci Flux'][sub_region].values
    unc = df['Sci Error'][sub_region].values
    
    def generative_model(m, b, A, mu, logw, int_wl = calcium_line):
        """Generate the model given parameters"""
        continuum = m * (wl - int_wl) + b
        w = np.exp(logw)
        gaussian = A * np.exp(-0.5*(wl-mu)**2/w**2)
        return continuum - gaussian
    
    def log_likelihood(theta):
        m, b, A, mu, logw = theta
        model = generative_model(m, b, A, mu, logw, int_wl = calcium_line)
        residual = flux - model
        chi_squared = np.sum(residual** 2 / unc**2)
        return -0.5 * chi_squared
    
    m_guess, b_guess, A_guess, mu_guess, logw_guess = 0.05, 1, 0.5, calcium_line+1, np.log(0.7)
    theta_guess = np.array([m_guess, b_guess, A_guess, mu_guess, logw_guess])
    
    pos = theta_guess + 1e-4 * np.random.randn(n_walkers, n_params) #intial guess position
    
    sampler = emcee.EnsembleSampler(n_walkers, n_params, log_likelihood)
    sampler.run_mcmc(pos, n_steps, progress=True);
    
    flat_samples = sampler.get_chain(discard=1000, thin=15, flat=True)

    A_draws = flat_samples[:,2]
    b_draws = flat_samples[:,1]
    m_draws = flat_samples[:,0]
    mu_draws = flat_samples[:,3]
    w_draws = np.exp(flat_samples[:, 4])

    EW = ((2*np.pi)**.5)*(A_draws*w_draws)/(m_draws*(mu_draws-calcium_line)+b_draws)
    EW

    ew_mean = np.mean(EW)
    ew_std = np.std(EW)
    print(ew_mean)
    print(ew_std)
    temp = {'ew':ew_mean, 'ew_unc':ew_std, 'date':date, 'star_name':obj, 'time':time, 'int_wv':calcium_line, 'qidx':qidx, 'jd':jd}
    df_results = df_results.append(temp, ignore_index=True)

  0%|          | 0/99 [00:00<?, ?it/s]

0 Goldilocks_20210224T105511_v1.0_0046.spectra.fits



 43%|███████████████████████████████████████████████████████████████████████████████▌                                                                                                           | 2126/5000 [00:03<00:04, 589.85it/s]


 86%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▍                          | 4291/5000 [00:07<00:01, 579.49it/s]


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5000/5000 [00:08<00:00, 595.16it/s]


...

-41.73649163379156
289.49358879122127
98 Goldilocks_20210304T102701_v1.0_0039.spectra.fits



 37%|█████████████████████████████████████████████████████████████████████                                                                                                                      | 1845/5000 [00:03<00:05, 526.33it/s]


 75%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▏                                              | 3747/5000 [00:07<00:02, 508.03it/s]


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5000/5000 [00:09<00:00, 524.96it/s]

1.7931218127576711
0.018803979042707763


In [45]:
df_results

date         ew      ew_unc  int_wv            jd    qidx  \
0   2021-02-24   1.623713    0.075764  8542.0  2.459270e+06  8486.0   
1   2021-02-24   1.757618    0.027705  8542.0  2.459270e+06  8486.0   
2   2020-04-28   1.652571    0.039899  8542.0  2.458968e+06  6437.0   
3   2020-04-28   1.830325    0.056830  8542.0  2.458968e+06  6437.0   
4   2020-04-28   1.811466    0.071233  8542.0  2.458968e+06  6437.0   
..         ...        ...         ...     ...           ...     ...   
94  2021-02-01   1.750809    0.016805  8542.0  2.459247e+06  8486.0   
95  2021-02-26   1.716331    0.024885  8542.0  2.459272e+06  8486.0   
96  2021-02-26   1.084856   12.255239  8542.0  2.459272e+06  8486.0   
97  2021-03-04 -41.736492  289.493589  8542.0  2.459278e+06  8486.0   
98  2021-03-04   1.793122    0.018804  8542.0  2.459278e+06  8486.0   

         star_name      time  
0        hat-p-67b  10:55:40  
1        hat-p-67b  11:04:43  
2   HAT-P-67b_IN_1  06:10:31  
3   HAT-P-67b_IN_1  06:16:12  
4   HAT-P-67b_IN_1  06:21:53  
..             ...       ...  
94       hat-p-67b  12:36:08  
95       hat-p-67b  10:28:30  
96       hat-p-67b  10:37:34  
97       hat-p-67b  10:18:26  
98       hat-p-67b  10:27:30  

[99 rows x 8 columns]

Great! It works!  Let's save the results to a csv file.

In [46]:
df_results.to_csv('C:/Users/jojoa/GitHub/disperse/data/preliminary_results_Ca.csv',index=False)